# Database parsing

In [1]:
import pandas, numpy as np
import parsingDatabaseUtils, re
import xml, itertools, collections, xml.etree.ElementTree as ET
import tqdm, importlib

In [2]:
casos = pandas.read_csv('Venezolanas/casos.csv', index_col = 0)
pacientes = pandas.read_csv('Venezolanas/pacientes.csv', index_col = 0)
pacientes.index = pacientes.index.map(str)

registros = pandas.read_csv('Venezolanas/registros.csv', index_col = 0)
registros.index = registros.index.map(str)

diagnosis = pandas.read_csv('Venezolanas/diagnosis.csv', index_col = 0)
procedimientos = pandas.read_csv('Venezolanas/procedimientos.csv', index_col = 0)
procedimientos.index = procedimientos.index.map(str)

procedimientosDesc = pandas.read_csv('Venezolanas/procedimientosID.csv', index_col = 0)
registrosByCaso = registros.groupby('Caso')

C:\Users\CMRC\Miniconda3\lib\site-packages\IPython\core\interactiveshell.py:3063: DtypeWarning: Columns (6,27,55) have mixed types.Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)
C:\Users\CMRC\Miniconda3\lib\site-packages\IPython\core\interactiveshell.py:3063: DtypeWarning: Columns (19) have mixed types.Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


In [3]:
parsingDatabaseUtils.cleanString('as\n ff,f d ')

'as\n ff f d'

In [4]:
classificationProcedures = {'H0165': 'o', 'H0193': 'o', 'H2120': 'o', 'H2379': 'o', 'H2383': 'o', 'H2386': 'o', 'H2407': 'o', 'H2415': 'o', 'H2595': 'o', 'H2684': 'o', 'H2849': 'o', 'H2852': 'o', 'H2880': 'o', 'H2882': 'o', 'H2884': 'o', 'H2892': 'o', 'H2901': 'o', 'H2904': 'o', 'H2910': 'o', 'H2916': 'o', 'H2959': 'o', 'H2963': 'o', 'H2974': 'a', 'H2975': 'a', 'H3038': 'o', 'H3065': 'o', 'H3066': 'o', 'H3078': 'o', 'H3089': 'p', 'H3092': 'p', 'H3094': 'p', 'H3099': 'a', 'H3100': 'a', 'H3108': 'o', 'H3109': 'o', 'H3111': 'o', 'H3114': 'o', 'H3118': 'o', 'H4421': 'o', 'H4494': 'o', 'H4496': 'o', 'HE020': 'o'}

## Select a case
Identify all  cases with an associated procedure

In [5]:
# Identify all  cases with an associated procedure

In [8]:
interventionToCase = {}
caseToProcedureBirths = {}
checkSeveralProcedures = []
for i,r  in tqdm.tqdm_notebook(registros.iterrows()):
    if isinstance(r.RegistroXML, str) and '<row NombreCampo="IdDescripcion"' in r.RegistroXML:
        et = ET.fromstring(r.RegistroXML)
        idDescripcionProcedimiento = et.find('.//row[@NombreCampo="IdDescripcion"]').get('ValorCampo')
        interventionToCase[idDescripcionProcedimiento] = (r.Caso, r.NumeroHistoria, i)
        procedureType = re.findall('<idProcedimiento>([a-zA-Z0-9]*)</idProcedimiento>', procedimientos.loc[idDescripcionProcedimiento].XmlDescripcion)[0]
        if classificationProcedures[procedureType] == 'p':
            
            #If it is the case that they need to stop labour because a c-section is needed
            if '<postDiagnosticoPrincipal>O821 - PARTO POR CESAREA DE EMERGENCIA</postDiagnosticoPrincipal>' in \
                procedimientos.loc[idDescripcionProcedimiento].XmlDescripcion:
                continue
                
            elif r.Caso in caseToProcedureBirths:
                r1 = caseToProcedureBirths[r.Caso]
                r2 =procedimientos.loc[idDescripcionProcedimiento]
                if r1.XmlDescripcion == r2.XmlDescripcion:
                    continue
                else:
                    checkSeveralProcedures.append(r.Caso)
                    print('error', r.Caso)
                    if r1.FechaRegistro > r2.FechaRegistro:
                        caseToProcedureBirths[r.Caso] = procedimientos.loc[idDescripcionProcedimiento]
            else:
                caseToProcedureBirths[r.Caso] = procedimientos.loc[idDescripcionProcedimiento]

error AD350190
error AD351571
error AD350755
error AD353436
error AD353902
error AD354284
error AD359075
error NN
error NN
error AD366060
error AD363741
error AD363741



In [7]:
importlib.reload(parsingDatabaseUtils)

<module 'parsingDatabaseUtils' from '/Users/gbernardino/toolsCMRC/parsingDatabaseUtils.py'>

In [54]:
import birthDatasetStructure
importlib.reload(birthDatasetStructure)
# Split in newborn
registrosByCaso = registros.groupby('Caso')
processedDatasets = {}
for c, p in tqdm.tqdm_notebook(caseToProcedureBirths.items()):
    if c not in casos.index:
        print('ERROR!', c)
        continue
    processedDatasets[c] = birthDatasetStructure.BirthDataset(c, casos.loc[c], p, registrosByCaso.get_group(c), pacientes)


ERROR! NN



In [68]:
for c, p in processedDatasets.items():
    
    if len(p.registrosRecienNacido) > 1:
        print(c, p.procTypeId,  len(p.registrosRecienNacido))


In [93]:
importlib.reload(parsingDatabaseUtils)
resSIP = {}
breakLoop = False
count = 0
for c, p in tqdm.tqdm_notebook(processedDatasets.items()):
    #resSIP[c] = parsingDatabaseUtils.getMotherData(p)
    #resSIP[c] = parsingDatabaseUtils.getInformationFromProcedureDescription(p)
    for k in p.registrosRecienNacido:
        resSIP[c] = parsingDatabaseUtils.getNewbornData(p, k)
df = pandas.DataFrame.from_dict(resSIP, orient = 'index')
#l = list(df[(df.VAR_0294 != df.VAR_0294) & (df.VAR_0293 != df.VAR_0293)].index)
#print(len(l))
print(count)


0


In [100]:
for c,  _ in df[df['sufrimientoFetal'] == 'SI'].iterrows():
    et = ET.fromstring(processedDatasets[c].epicrisis.RegistroXML)
    print(parsingDatabaseUtils.findInXML('MedicamentosAdministrado', et ))


Fecha: 04/12/2017
-19972965-01 - SOLUCION SALINA 0.9 %- Cantidad: 2
-201128 - Jeringa Desechable 1 ml x 27 G/ 1/2&amp;quot; - Cantidad: 2
-51076-02 - SOLUCION SALINA 0.9 % - Cantidad: 1
-IM5034 - MORFINA CLORHIDRATO - Cantidad: 1
-IM5059 - BUPIVACAINA+DEXTROSA (BUPIROP PESADO) - Cantidad: 1
-IM5064 - LACTATO DE RINGER - Cantidad: 6
-IM5065 - LACTATO DE RINGER - Cantidad: 1
-IM5093 - RECIPIENTE DE SUCCION FLEXIBLE (LINER) de 3 LT - Cantidad: 1
-INS001 - ABOCATH NO. 18 - Cantidad: 1
-INS007 - EQUIPO MACROGOTEO - Cantidad: 1
-INS016 - SONDA NELATON # 16 - Cantidad: 1
-INS039 - VICRYL 1 CT-1(HR37S) x 90 CM - Cantidad: 1
-INS042 - AGUJA ESPINAL TIPO QUINCKE # 27 X 3 1/2 x 90 MM - Cantidad: 1
-INS089 - NYLON 3/0 (CDSS24) AGUJA CURVA - Cantidad: 1
-INS1019 - CATGUT 0 CT/1 ( HR37S) x 70 CM - Cantidad: 1
-INS1020 - CATGUT 1 CT/1 (HR37S) x 90 CM - Cantidad: 1
-INS121 - SONDA NELATON # 8 - Cantidad: 1
-INS127 - LAPIZ DE ELECTROBISTURI - Cantidad: 1
-INS225 - Jeringa Desechable 10 ml x 21 G/1 1/2

In [90]:
df[df['VAR_0425'].isna()]

VAR_0284    VAR_0283 VAR_0198  partoVag  \
AD215646  13/03/2017  06:00 p.m.        0      True   
AD239256  20/07/2017  12:50 p.m.       40      True   
AD254941  11/10/2017  12:35 p.m.        0      True   
AD276859  22/02/2018  10:35 p.m.       39      True   
AD292345  01/06/2018  06:43 p.m.       40      True   
...              ...         ...      ...       ...   
AD366859  07/01/2020  09:33 p.m.       40     False   
AD367379  12/01/2020  09:10 p.m.       40     False   
AD368225  20/01/2020  06:10 p.m.               True   
AD368521  21/10/2019  06:22 p.m.              False   
AD368707  23/01/2020  10:22 a.m.               True   

                                       VAR_0321 VAR_0310 VAR_0311 VAR_0314  \
AD215646              8 al min y  9 a los 5 min        B     2860       43   
AD239256              8 AL MIN Y 9  A LOS 5 MIN        B     3020       49   
AD254941                                    8/9        A     2500       48   
AD276859  AL MINUTO 8/10 y A LOS 5 MINUTOS 9/10        B     2950       48   
AD292345           8 AL MIN Y 9 A LOS 5 MINUTOS        A     3790       52   
...                                         ...      ...      ...      ...   
AD366859   8/10 AL MINUTO, 9/10 A LOS 5 MINUTOS        B     3270       52   
AD367379      9 al min y 10 a los 5 min                A     3120       50   
AD368225                                      0        A     2960       49   
AD368521                8AL MIN -9 A LOS 5 MIN         A     2900       50   
AD368707                8 AL MIN- 9 A LOS 5 MIN        B     3400       53   

         VAR_0313 VAR_0040 VAR_0041 VAR_0046 VAR_0047 VAR_0425 VAR_0343  \
AD215646       34        4        0        4        0      NaN        A   
AD239256       33        2        1        1        0      NaN        A   
AD254941       31        2        1        1        0      NaN        B   
AD276859       34        2        0        2        0      NaN        A   
AD292345       35        1        0        1        0      NaN        A   
...           ...      ...      ...      ...      ...      ...      ...   
AD366859       36        2        0        2        2      NaN        A   
AD367379       34       01        0       01       01      NaN        A   
AD368225       32        3        0       03        0      NaN      NaN   
AD368521       34       02        1        1        0      NaN        A   
AD368707       35        3        1        2        0      NaN        A   

         VAR_0381 VAR_0330  
AD215646      NaN      NaN  
AD239256      NaN      NaN  
AD254941      NaN      NaN  
AD276859      NaN      NaN  
AD292345      NaN      NaN  
...           ...      ...  
AD366859      NaN      NaN  
AD367379      NaN      NaN  
AD368225      NaN      NaN  
AD368521      NaN      NaN  
AD368707      NaN      NaN  

[75 rows x 17 columns]

In [256]:
for _, p in processedDatasets['AD218865'].registrosRecienNacido['796790'].items():
    parsingDatabaseUtils.prettyPrintXML(p.RegistroXML)
    print('------')

<?xml version="1.0" ?>
<C Asunto="EVOLUCION" Caso="AD218865" CentroA="01" Diagnostico="NULL" IdPaciente="164688" Modulo="01" Padre="796790" PlanAdm="100" Prestador="73086292" Raiz="165" Registro="166">
	<row NombreCampo="CodigoPlanAdministradora" NombreTabla="CamposTexto" ValorCampo="100|0001"/>
	<row NombreCampo="DescripcionNota" NombreTabla="CamposMemo" ValorCampo="&lt;B&gt;
&lt;P align=center&gt;EVOLUCI&#211;N&amp;nbsp; &lt;/P&gt;&lt;/B&gt;
&lt;P align=center&gt;　&lt;B&gt;RN CON DIAGNOSTICO DE: &lt;/B&gt;&lt;BR&gt;1. RNTAEG (29/03/2017&amp;nbsp;10:25PM)&lt;BR&gt;2. RIESGO DE SEPSIS POR NO CONTROL PRENATAL&lt;BR&gt;&lt;STRONG&gt;PESO:&lt;/STRONG&gt;&amp;nbsp;3210&amp;nbsp; gm&lt;STRONG&gt;TALLA: 50 cm, PC: 32 PT: 33&lt;/STRONG&gt;&lt;/P&gt;
&lt;P align=justify&gt;&lt;STRONG&gt;GRUPO SANGUINEO&amp;nbsp;DE MADRE: A+ &lt;/STRONG&gt;&lt;/P&gt;
&lt;P align=justify&gt;&lt;STRONG&gt;SUBJETIVO:&lt;/STRONG&gt; MADRE REFIERE QUE EL PACIENTE PASO BUENA NOCHE, TOLERANDO VIA ORAL, NIEGA FIEBRE, N

In [240]:
df['VDRL'] == df['VDRL']

AD182404     True
AD191656     True
AD184378    False
AD206592    False
AD209823     True
            ...  
AD368734     True
AD368665     True
AD368707     True
AD368729     True
AD368822    False
Name: VDRL, Length: 1871, dtype: bool

In [177]:
len(df.loc[df['VAR_0314'] != df['VAR_0314']])

33

In [132]:
errorCount = 0
for c,v in resSIP.items():
    if len(v) == 0:
        errorCount += 1
print(errorCount)
        

8


In [140]:
from __future__ import print_function
from ipywidgets import interact, interactive, fixed, interact_manual
def f(c):
    parsingDatabaseUtils.prettyPrintXML(processedDatasets[c].procedure.XmlDescripcion)
interact(lambda i: f(l[i]), i = (0, len(l)))

interactive(children=(IntSlider(value=21, description='i', max=43), Output()), _dom_classes=('widget-interact'…

<function __main__.<lambda>(i)>

In [17]:
noEpicrsis = []
noIngreso = []

noDischarge = []
for c, p in processedDatasets.items():
    if len(p.registersNewborn) == 0:
        noDischarge.append(c)
    if p.ingreso is None:
        noIngreso.append(c)
print(len(noIngreso), len(noDischarge), len(processedDatasets))

83 58 2044


In [110]:
count = 0
for c, p in processedDatasets.items():
    if p.epicrisis is None:
        continue
    et = ET.fromstring(p.epicrisis.RegistroXML)
    ant = parsingDatabaseUtils.fullCleanTxt(parsingDatabaseUtils.findInXML('AntecedentesHTML', et))
    if not 'paracli' in ant:
        count += 1
    else:
        print(ant)

personales 
 7 > menarquia 15
vida sexual 27 
vida obstetrica 28
g1p0a0c0
fum 15/01/16 hoy embarazo de 39.6 semanas 
companeros sexuales 1
controles prenatales 3 (pobremente controlado)
tipo de sangre. o+
planificacion niega 

ecografias 
08/junio/16 embarazo de 20 3 semanas para hoy embarazo de 39,4 semanas
27/junio/16 embarazo de 23 semanas para hoy embarazon de 41 semanas
22/agosto/16 embarazo de 32 semanas para hoy embarzo de 40,3 semanas

paraclinicos 
08/junio/16 hemograma hb 10,4 hto 31 leu 7,700
27/junio/16 antitoxoplasma ( )
no trae vih ni vdrl


 5 > niega
 familiares 
 niega
 alergicos 
 
 quirurgicos
personales 
 1 > asma 
 
 7 > g 1 p 0 a 0 c 0 
fum no recuerda 
menarquia 11 
vida marital 15 
vida obstetrica 18 
companerops sexuales 1 
tipo de sangre o+ 
 
ecografias 
6/6/2016 embarazo de 21 semanas hoy 34.3 
 
paraclinicos 
12 de julio del 2016 hemograma hb 10.9gr/dl htc 34.5% plq 283.000 leu 10.100 
 familiares 
 niega 
 alergicos 
 
 quirurgicos
personales 
 2 > litotri

In [107]:
count

721

In [92]:
c = 'AD284225'
k = next(iter(processedDatasets[c].registrosRecienNacido.keys()))
parsingDatabaseUtils.prettyPrintXML(processedDatasets[c].registrosRecienNacido[k][k].RegistroXML)


<?xml version="1.0" ?>
<RegistroClinico VersionEsquemaGuardado="1.1">
	<Cabecera Asunto="Registro del recién nacido" Caso="AD284225" CentroA="01" CodigoDiagnosticoRelacionado1="P008" CodigoDiagnosticoRelacionado2="" CodigoDiagnosticoRelacionado3="" Diagnostico="Z380" IdPaciente="184931" Modulo="03" Padre="Padre" PlanAdm="100" Prestador="1143342901" Raiz="NULL" Registro="165"/>
	<Cuerpo>
		<row NombreCampo="InputText_Fecha" NombreTabla="CamposTexto" ValorCampo="12/04/2018"/>
		<row NombreCampo="PlanAdministradora" NombreTabla="CamposTexto" ValorCampo="DEPARTAMENTO ADMINISTRATIVO DISTRITAL DE SALUD (DADIS) / DADIS CARTAGENA SISBENIZADO"/>
		<row NombreCampo="CodigoPlanAdministradora" NombreTabla="CamposTexto" ValorCampo="100"/>
		<row NombreCampo="InputText_NumeroCertificadoNacidoVivo" NombreTabla="CamposTexto" ValorCampo="146711694"/>
		<row NombreCampo="InputText_NombreMadre" NombreTabla="CamposTexto" ValorCampo="TATIANA KATIUSCA GUANIPA VARGA"/>
		<row NombreCampo="InputText_NombrePad

In [239]:
c = list(processedDatasets.keys())[884]
for c in processedDatasets.keys():
    if 'SEPSIS' in processedDatasets[c].epicrisis.RegistroXML:
        print(c)
        parsingDatabaseUtils.prettyPrintXML(processedDatasets[c].epicrisis.RegistroXML)

AD218865
<?xml version="1.0" ?>
<C Asunto="Epicrisis de la Historia Ingreso de Urgencias" Caso="AD218865" CentroA="01" CodigoDiagnosticoRelacionado1="O839" CodigoDiagnosticoRelacionado2="" CodigoDiagnosticoRelacionado3="" Diagnostico="Z340" IdPaciente="164688" Modulo="01" Padre="AD218865" PlanAdm="100" Prestador="1047400244" Raiz="01" Registro="450">
	<row NombreCampo="Antecedentes" NombreTabla="CamposTexto" ValorCampo=""/>
	<row NombreCampo="AntecedentesHTML" NombreTabla="CamposTexto" ValorCampo="- PERSONALES:
  7-&amp;gt; MENARQUIA: 14 A&#209;OS.
VIDA MARITAL: 16 A&#209;OS.
VIDA OBSTETRICA: 17 A&#209;OS.
G2 P0 C0 A0  
CICLOS: 5X30
FUM: 22.06.2016
EG X FUM: 39.2
COMPA&#209;EROS SEXUALES: 1
GRUPO SANGUINEO: A POSITIVO
PLANIFICACI&#211;N FAMILIAR: NIEGA
CONTROLES PRENATALES: 6

*ECOGRAFIA: 6.02.2017: EMBARAZO DE 32 SEMANAS
- FAMILIARES:
  NIEGA
- AL&#201;RGICOS:
  
- QUIR&#218;RGICOS:"/>
	<row NombreCampo="AplicaCuidadoEnfermeria" NombreTabla="CamposBoolean" ValorCampo="false"/>
	<row N

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [151]:
df.to_csv('test.csv')

In [90]:
c = list(processedDatasets.keys())[244]
parsingDatabaseUtils.prettyPrintXML(processedDatasets[c].epicrisis.RegistroXML)

<?xml version="1.0" ?>
<C Asunto="Epicrisis de la Historia Ingreso de Urgencias" Caso="AD336169" CentroA="01" CodigoDiagnosticoRelacionado1="Z348" CodigoDiagnosticoRelacionado2="" CodigoDiagnosticoRelacionado3="" Diagnostico="O623" IdPaciente="206122" Modulo="01" Padre="AD336169" PlanAdm="100" Prestador="1128057935" Raiz="01" Registro="450">
	<row NombreCampo="Antecedentes" NombreTabla="CamposTexto" ValorCampo=""/>
	<row NombreCampo="AntecedentesHTML" NombreTabla="CamposTexto" ValorCampo="- PERSONALES:
  1-&amp;gt;  ASMA

  2-&amp;gt; NIEGA

  5-&amp;gt;  NIEGA

  7-&amp;gt; 
MENARQUIA: 8 A&#209;OS 
INICIO DE VIDA SEXUAL: 15 A&#209;OS
INICIO DE VIDA OBSTETRICA: 15 A&#209;OS 
G1 P0 C0 A0
PERIODOS MENSTRUALES:  REGULARES
FUM:  NO SABE 
PLANIFICACION FAMILIAR: NIEGA
COMPA&#209;EROS SEXUALES: 1
ITS: NIEGA 
GRUPO SANGUINEO: A+
CONTROLES PRENALES: 6

PACIENTE NO TRAE PARACLINICOS 

ECOGRAFIA 
14/1/19 EMB 25.3 SEMANAS PARA HOY 39.6 SEMANAS 
5/9/18 EMB 6.1 SEMANA S PARA HOY 39.2 SEMANAS * 7-&a

In [157]:
# read paraclinics. Assume that the date is just bmonthre them, or in the same line

pos = ['pos', '\+', 'reac']
neg = ['neg', '-', 'no']
vih1  = 'vih\s*[1i]'
vih2 = 'vih\s*(:?2|ii)'
vih12 = 'vih\s*[1i]\s*(:?2|ii)'
prt = '(:?PRUEBA RAPIDA TREPONEMICA|PRT)'
vdrl = '(:?VDRL|SIF[A-Z]*|RPR)'
floatParse = '[0-9]*[\.,]?[0-9]+'

hematology = {
'HCT' : '(HCT|HTO|HTC|HEMATO[A-Z]*)',
'HB' : '(HB|HEMOGLOB[A-Z]*)',
'LEU' : '(LEU[A-Z]*)',
'NEU' : '(NEU[A-Z]*)',
'LIN' : '(LIN)',
'MONO' : '(MONO[A-Z]*)',
'PLAQ' : '(PL[A-Z]*|PQT)'}

meses = ['ENERO', 'FEBRERO', 'MARZO', 'ABRIL', 'MAYO', 'JUNIO', 'JULIO', 'AGOSTO', 'SEPTIEMBRE', 'OCTUBRE', 'NOVIEMBRE', 'DICIEMBRE']
meses = meses + list(map(lambda s: s[:3], meses))
sep= '\s*[,;:]?\s*'
separadorFecha = '(?:[\.\\/-]|DE|DEL|\s)'
date =  '\(?' +  '((?:[0-9]+)'+ sep + separadorFecha + sep + '(?:[0-9]+|%s)'%  '|'.join(meses) + \
                       sep + separadorFecha + sep + '(?:[0-9]+))' + '\)?' 

def parseParaclinics(r):
    if not isinstance(r, str):
        rET = ET.fromstring(r.RegistroXML)
        rTxt = parsingDatabaseUtils.fullCleanTxt(parsingDatabaseUtils.findInXML('AntecedentesHTML', rET))
        rTxt = parsingDatabaseUtils.removeWords(rTxt, ['de', 'y', 'a', 'el', 'los'])
    else:
        rTxt = r
        
        
    lastDate = None
    results = collections.defaultdict(dict)
    results['text'] = rTxt
    if re.findall('(no|sin|ni) (prese[a-z]*|tien[a-z]*|tra[a-z]*)(\s)*para', rTxt):
        results['sinParaclinicos'] = True
        return results
    
    for i, l in enumerate(rTxt.splitlines()):
        l = ' ' + l
        d = re.findall(date, l, re.IGNORECASE)
        if len(d) == 1.:
            date = dateparser.parse(d[0])
            lastDate ='%02d/%02d/%d' %(date.days, date.months, date.year)
        elif len(d):
            lastDate = None
        if len(d) <= 1:
            #Hematology
            for p, v in hematology.items():
                hematologyRes = re.findall('%s (%s)[^x]' % (v, floatParse), l, re.IGNORECASE)
                if hematologyRes:
                    results[lastDate][p] = hematologyRes[0][1]

            #sifilis
            sif1 = ' ' + vdrl + " (%s)" % '|'.join(pos + neg)
            searchSif1 = re.findall(sif1, l, re.IGNORECASE)
            sif2 = ' ' + prt + " (%s)" % '|'.join(pos + neg)    
            searchSif2 = re.findall(sif2, l, re.IGNORECASE)
            if searchSif1:
                results[lastDate]['vdrl'] =searchSif1[0][1] in pos
            if searchSif2:
                results[lastDate]['prt'] =searchSif2[0][1] in pos
            # TODO: vih
    return results

In [158]:
paraClinics = {}
for c, p in processedDatasets.items():
    if p.epicrisis is None:
        continue
    paraClinics[c] = parseParaclinics(p.epicrisis)
    

In [ ]:
def paraclinicsToDF(p):
    res = {}
    res['noParaclinicalTestsConfirmed'] = 'sinParaclinicos' in res
    i = 0
    for date in sorted(p.keys()):
        if date == 'sinParaclinicos': 
            continue
        res['day_%d' % i] = date
        for k, v in p[date].items():
            res['day_%d' % i + k] = v 
        i += 1
    return res

In [ ]:
for c, p in paraClinics.items():
    if len(p) != 1:
        print(paraClinics[c]['text'])
        print('-----------------')
        for k in p:
            if k != 'text':
                print(k, p[k])
        print('-----------------')

personales 
 7 > menarquia 15
vida sexual 27 
vida obstetrica 28
g1p0a0c0
fum 15/01/16 hoy embarazo 39.6 semanas 
companeros sexuales 1
controles prenatales 3 (pobremente controlado)
tipo sangre. o+
planificacion niega 

ecografias 
08/junio/16 embarazo 20 3 semanas para hoy embarazo 39,4 semanas
27/junio/16 embarazo 23 semanas para hoy embarazon 41 semanas
22/agosto/16 embarazo 32 semanas para hoy embarzo 40,3 semanas

paraclinicos 
08/junio/16 hemograma hb 10,4 hto 31 leu 7,700
27/junio/16 antitoxoplasma ( )
no trae vih ni vdrl


 5 > niega
 familiares 
 niega
 alergicos 
 
 quirurgicos
-----------------
08/junio/16 {'HCT': '31', 'HB': '10,4', 'LEU': '7,70'}
-----------------
personales 
 1 > asma 
 
 7 > g 1 p 0 0 c 0 
fum no recuerda 
menarquia 11 
vida marital 15 
vida obstetrica 18 
companerops sexuales 1 
tipo sangre o+ 
 
ecografias 
6/6/2016 embarazo 21 semanas hoy 34.3 
 
paraclinicos 
12 julio del 2016 hemograma hb 10.9gr/dl htc 34.5% plq 283.000 leu 10.100 
 familiares 
 ni

In [ ]:
def merge2DF(df1, df2):
    """
    Returns the merge of 2 df with the same index (1 to 1)
    In case of columns with the same name, check if the values are the same (or one of them is NA)
    Creates new error column to see where there has been problems
    """
    pass